In [36]:
import pandas as pd
import numpy as np

from bokeh.plotting import figure, show, output_notebook
from bokeh.transform import linear_cmap
from bokeh.palettes import Turbo256
from bokeh.models import HoverTool

output_notebook()

Loading BokehJS ...

In [38]:
df.columns

Index(['id_odsp', 'event_team', 'opponent', 'side', 'event_type',
       'event_type2', 'player', 'player2', 'shot_place', 'shot_outcome',
       'is_goal', 'location', 'bodypart', 'assist_method', 'situation',
       'minute', 'event_type_label', 'is_shot', 'location_label', 'zone_group',
       'shot_outcome_label', 'shot_result', 'x', 'y'],
      dtype='object')

In [42]:
df = pd.read_csv("shots_heatmap_ready.csv")
df[["x", "y"]].head()

x          y
0  100.0  44.482853
1   88.0  39.504439
2  100.0  32.906353
3   88.0  38.584148
4   88.0  37.720044

In [48]:
p = figure(
    title="Football Shot Map",
    width=900,
    height=500,
    x_range=(0, 100),
    y_range=(0, 65),
    toolbar_location="right"
)

# pitch background
p.rect(x=50, y=32.5, width=100, height=65, fill_color="#3f995b", line_color=None)

# halfway line
p.line([50, 50], [0, 65], line_color="white", line_width=2)

# center circle
theta = np.linspace(0, 2*np.pi, 200)
p.line(50 + 9*np.cos(theta), 32.5 + 9*np.sin(theta), color="white", line_width=2)

# penalty boxes
p.rect(16.5, 32.5, width=33, height=40.3, fill_color=None, line_color="white", line_width=2)
p.rect(83.5, 32.5, width=33, height=40.3, fill_color=None, line_color="white", line_width=2)

# goal boxes
p.rect(5.5, 32.5, width=11, height=18.3, fill_color=None, line_color="white", line_width=2)
p.rect(94.5, 32.5, width=11, height=18.3, fill_color=None, line_color="white", line_width=2)

# penalty spots
p.circle([11, 89], [32.5, 32.5], size=6, color="white")

# clean look
p.grid.visible = False
p.axis.visible = False

In [50]:
p.circle(
    df["x"],
    df["y"],
    size=4,
    fill_color="lightgray",
    fill_alpha=0.35,
    line_alpha=0
)

GlyphRenderer(id='p1523', ...)

In [58]:
print(hex_renderer.data_source.data.keys())

dict_keys(['q', 'r', 'c'])


In [76]:
# 1️⃣ Filter hexbin to attacking area
df_hex = df[df["x"] > 70]

# 2️⃣ Draw hexbin from filtered data
hex_renderer, _ = p.hexbin(
    df_hex["x"],
    df_hex["y"],
    size=4
)

# 3️⃣ Keep it subtle
hex_renderer.glyph.fill_alpha = 0.6
hex_renderer.level = "underlay"

In [78]:
p.add_tools(
    HoverTool(
        tooltips=[("Shots", f"@{count_field}")],
        renderers=[hex_renderer]
    )
)

In [80]:
p.x_range.start = 0
p.x_range.end = 100
p.y_range.start = 0
p.y_range.end = 65

show(p)